# xnatpy: a pythonic feeling interface to XNAT

xnatpy attempts to expose objects in XNAT as native feeling Python objects. The objects reflect the state of XNAT and changes to the objects automatically update the server.

To facilitate this xnatpy scans the server xnat.xsd and creates a Python class structure to mimic this is well as possible.

Current features:
* automatic generate of most data structures from the xnat.xsd
* easy exploration of data
* easy getting/setting of custom variables
* easy downloading/uploading of data
* using the prearchive
* the import service

Missing features (aka my TODO list):
* good support for the creation of objects
* good support for searches

### Some imports and helper code used later on

In [1]:
import os
import random

## getting started

First we need to set up an xnatpy session. 
The session scans the xnat.xsd, creates classes,
logs in into XNAT, and keeps the connection alive
using a hearbeat.

In [2]:
import xnat
print('Loaded xnatpy version {}'.format(xnat.__version__))
session = xnat.connect('https://central.xnat.org', user='xnatpydemo', password='demo2017')

Loaded xnatpy version 0.3.2


This will create an XNAT session object, which is the base class for all operations with the XNAT server. It also create a keep alive thread that makes sure the session is polled every 14 minutes to keep the connection alive.

To save your login you set up a .netrc file with the correct information about the target host.
A simple example of a .netrc file can be found at  [http://www.mavetju.org/unix/netrc.php](http://www.mavetju.org/unix/netrc.php).

It is possible to set the login information on connect without using a netrc file.

All the options of the connect function can be found in the docstring. You can turn of certificate verification for self signed certificates, change log options, disbale use of extension type.

In [3]:
help(xnat.connect)

Help on function connect in module xnat:

connect(server, user=None, password=None, verify=True, netrc_file=None, debug=False, extension_types=True, loglevel=None, logger=None)
    Connect to a server and generate the correct classed based on the servers xnat.xsd
    This function returns an object that can be used as a context operator. It will call
    disconnect automatically when the context is left. If it is used as a function, then
    the user should call ``.disconnect()`` to destroy the session and temporary code file.
    
    :param str server: uri of the server to connect to (including http:// or https://)
    :param str user: username to use, leave empty to use netrc entry or anonymous login.
    :param str password: password to use with the username, leave empty when using netrc.
                         If a username is given and no password, there will be a prompt
                         on the console requesting the password.
    :param bool verify: verify the https ce

## Session object basic functionality

The session is the main entry point for the module. It has some basic REST functions on which the rest of the package is built, these are the get, put, post, delete, head, download and upload methods. They are very similar to the requests package but contain helpers that build the total URL from a REST path and check the resulting HTML code and content somewhat.

In [4]:
help(session.get)

Help on method get in module xnat.session:

get(self, path, format=None, query=None, accepted_status=None) method of xnat.session.XNATSession instance
    Retrieve the content of a given REST directory.
    
    :param str path: the path of the uri to retrieve (e.g. "/data/archive/projects")
                     the remained for the uri is constructed automatically
    :param str format: the format of the request, this will add the format= to the query string
    :param dict query: the values to be added to the query string in the uri
    :param list accepted_status: a list of the valid values for the return code, default [200]
    :returns: the requests reponse
    :rtype: requests.Response



In [5]:
response = session.get('/data/projects/xnatpydemo/subjects')
print(response)
print('\n\n')
print(response.text)
print('\n\n')
print(session.get_json('/data/projects/xnatpydemo/subjects'))

<Response [200]>



{"ResultSet":{"Result":[{"project":"xnatpydemo","insert_user":"xnatpydemo","ID":"CENTRAL_S06138","insert_date":"2017-10-15 09:05:36.025","label":"Case001","URI":"/data/subjects/CENTRAL_S06138"},{"project":"xnatpydemo","insert_user":"xnatpydemo","ID":"CENTRAL_S06139","insert_date":"2017-10-15 10:22:35.673","label":"archive_subject_489","URI":"/data/subjects/CENTRAL_S06139"},{"project":"xnatpydemo","insert_user":"xnatpydemo","ID":"CENTRAL_S06140","insert_date":"2017-10-15 10:23:40.707","label":"archive_subject_981","URI":"/data/subjects/CENTRAL_S06140"},{"project":"xnatpydemo","insert_user":"xnatpydemo","ID":"CENTRAL_S06137","insert_date":"2017-10-15 08:56:12.551","label":"subject001","URI":"/data/subjects/CENTRAL_S06137"},{"project":"xnatpydemo","insert_user":"xnatpydemo","ID":"CENTRAL_S06141","insert_date":"2017-10-15 10:25:19.826","label":"archive_subject_158","URI":"/data/subjects/CENTRAL_S06141"}], "totalRecords": "5"}}



{u'ResultSet': {u'totalRecords': u'5', u

## xnatpy objects

xnatpy creates a class hierarchy based on the xnat.xsd and other schemas it can find on the XNAT server (including extension types). These classes mirror the behaviour described in the xsd as best as possible in Python. The idea is that it feels like you are manipulating python objects, while in fact you are working on the XNAT server. It completely abstract the REST interface away.

The entry points for this are the projects, subject and experiments properties in the session object:

In [6]:
sandbox = session.projects['xnatpydemo']
print(sandbox)

<ProjectData xnatpydemo>


In [7]:
sandbox.description

u'Random_project_description_4'

In [8]:
new_description = 'Random_project_description_{}'.format(random.randint(0, 100))
print('Changing description to: {}'.format(new_description))
sandbox.description = new_description

Changing description to: Random_project_description_76


In [9]:
sandbox.description

u'Random_project_description_76'

In [10]:
# Get a list of the subjects
sandbox.subjects

<XNATListing {(CENTRAL_S06138, Case001): <SubjectData Case001>, (CENTRAL_S06139, archive_subject_489): <SubjectData archive_subject_489>, (CENTRAL_S06140, archive_subject_981): <SubjectData archive_subject_981>, (CENTRAL_S06137, subject001): <SubjectData subject001>, (CENTRAL_S06141, archive_subject_158): <SubjectData archive_subject_158>}>

Note that the entries are in the form `(CENTRAL_S01824, custom_label): <SubjectData CENTRAL_S01824>`. This does not mean that the key is `(CENTRAL_S01824, custom_label)`, but that both the keys `CENTRAL_S01824` and `custom_label` can be used for lookup. The first key is always the XNAT internal id, the second key is defined as:
* project: the name
* subject: the label
* experiment: the label
* scan: the scantype
* resource: label
* file: filename

In [11]:
subject = sandbox.subjects['subject001']

In [12]:
print('Before change:')
print('Gender: {}'.format(subject.demographics.gender))
print('Initials: {}'.format(subject.initials))

# Change gender and initials. Flip them between male and female and JC and PI
subject.demographics.gender = 'female' if subject.demographics.gender == 'male' else 'male'
subject.initials = 'JC' if subject.initials == 'PI' else 'PI'

print('After change:')
print('Gender: {}'.format(subject.demographics.gender))
print('Initials: {}'.format(subject.initials))

Before change:
Gender: female
Initials: PI
After change:
Gender: male
Initials: JC


There is some basic value checking before assignment are carried out. It uses the xsd directives when available. For example:

In [13]:
subject.demographics.gender = 'martian'

ValueError: gender has to be one of: "male", "female", "other", "unknown", "M", "F"

### Creating an xnatpy object from a REST path

If you have a huge database and would like to skip (parts of) the listings, 
you can create an XNAT object straight from a REST path. It will automatically
figure out the correct class from the XNAT response. This object then can be use
just as any other xnatpy object:

In [14]:
subject = session.create_object('/data/projects/xnatpydemo/subjects/Case001')
print(subject)
print(subject.experiments)

<SubjectData Case001>
<XNATListing {(CENTRAL_E11129, Case001): <MrSessionData Case001>}>


### XNAT to xnatpy class mapping

You can see the mapping of classes created by xnatpy using the class lookup:

In [15]:
import pprint
pprint.pprint(session.XNAT_CLASS_LOOKUP)

{u'adrc:ADRCClinicalData': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.ADRCClinicalData'>,
 u'arc:fieldSpecification': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.FieldSpecification'>,
 u'arc:pathInfo': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.PathInfo'>,
 u'arc:pipelineData': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.PipelineData'>,
 u'arc:pipelineParameterData': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.PipelineParameterData'>,
 u'arc:project': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.Project'>,
 u'arc:property': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.Property'>,
 u'cat:catalog': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.Catalog'>,
 u'cat:dcmCatalog': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.DcmCatalog'>,
 u'cat:dcmEntry': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.DcmEntry'>,
 u'cat:entry': <class 'xnat_gen_973887e06d7184e81993569fbb9198db.Entry'>,
 u'cnda:adrc_psychometrics': <class 'xnat_gen_973887e06

In [16]:
print('Subject XSI: {}'.format(subject.__xsi_type__))
print('Subject xpath: {}'.format(subject.xpath))
print('Subject demographics XSI: {}'.format(subject.demographics.__xsi_type__))
print('Subject demographics XSI: {}'.format(subject.demographics.xpath))

Subject XSI: xnat:subjectData
Subject xpath: xnat:subjectData
Subject demographics XSI: xnat:demographicData
Subject demographics XSI: xnat:subjectData/demographics[@xsi:type=xnat:demographicData]


## Custom Variables

In xnatpy custom variables are exposed as a simple mapping type that is very similar to a dictionary.

In [17]:
print(subject.fields)
subject.

<XNATSimpleListing {}>


In [18]:
# Add something
subject.fields['test_field'] = 42
print(subject.fields)

<XNATSimpleListing {u'test_field': u'42'}>


In [19]:
subject.fields['test_field']

u'42'

Note that custom variables are always stored as string in the database. So the value is always casted to a string. Also the length of a value is limited because they are passed on the requested url.

The custom variables are by default not visible in the UI, there are special settings in the UI to make them appear. Defined variables in the UI that are not set, are just not appearing in the fields dictionary.

To avoid `KeyError`, it would be best to use `subject.fields.get('field_name')` which returns None when not available.

## Downloading stuff

Downloading with xnatpy is fairly simple. Most objects that are downloadable have a `.download` method. There is also a `download_dir` method that downloads the zip and unpacks it to the target directory.

In [20]:
download_dir = os.path.expanduser('~/xnatpy_temp')
print('Using {} as download directory'.format(download_dir))
if not os.path.exists(download_dir):
    os.makedirs(download_dir)
sandbox.subjects['Case001'].download_dir(download_dir)

Using /home/hachterberg/xnatpy_temp as download directory


 45.6 MiB |         #                       |   1.1 MiB/s Elapsed Time: 0:00:40


# import service

xnatpy exposes the import service of xnat (documentation at https://xnat.readthedocs.io/en/latest/xnat.html#xnat.services.Services )

In [21]:
zip_file = os.path.join(download_dir, 'Case001.zip')
sandbox.subjects['Case001'].experiments['Case001'].download(zip_file)

In [22]:
subject_name = "import_subject_{}".format(random.randint(0, 999))
print('Importing under new subject: {}'.format(subject_name))
session.services.import_(zip_file, destination='/prearchive', project='xnatpydemo', subject=subject_name)

Importing under new subject: import_subject_132


<PrearchiveSession xnatpydemo/20171016_052006805/Case001>

## Prearchive

xnatpy also offers an interface to the prearchive using the session.prearchive.session method, which list the PrearchiveSessions. These object can be used to inspect a session in the prearchive and to manipulate it (e.g. delete, move, archive)

More info can be found at https://xnat.readthedocs.io/en/latest/xnat.html#xnat.prearchive.PrearchiveSession

In [23]:
print("-- Before archive --")
print('prearchive:')
print session.prearchive.sessions()
print('project:')
print sandbox.subjects

# Create a new name for subject and experiment
pas = session.prearchive.sessions()[0]
nr = random.randint(0, 999)
subject_name = "archive_subject_{}".format(nr)
experiment_name = "archive_exp_{}".format(nr)
print('Using name: {} / {}'.format(subject_name, experiment_name))

# Archive subject under different name
pas.archive(subject=subject_name, experiment=experiment_name)

print("-- After archive --")
print('prearchive:')
print session.prearchive.sessions()
print('project:')
print sandbox.subjects.clearcache()
print sandbox.subjects

-- Before archive --
prearchive:
[<PrearchiveSession xnatpydemo/20171016_052006805/Case001>]
project:
<XNATListing {(CENTRAL_S06138, Case001): <SubjectData Case001>, (CENTRAL_S06139, archive_subject_489): <SubjectData archive_subject_489>, (CENTRAL_S06140, archive_subject_981): <SubjectData archive_subject_981>, (CENTRAL_S06137, subject001): <SubjectData subject001>, (CENTRAL_S06141, archive_subject_158): <SubjectData archive_subject_158>}>
Using name: archive_subject_520 / archive_exp_520
-- After archive --
prearchive:
[]
project:
None
<XNATListing {(CENTRAL_S06138, Case001): <SubjectData Case001>, (CENTRAL_S06139, archive_subject_489): <SubjectData archive_subject_489>, (CENTRAL_S06140, archive_subject_981): <SubjectData archive_subject_981>, (CENTRAL_S06137, subject001): <SubjectData subject001>, (CENTRAL_S06141, archive_subject_158): <SubjectData archive_subject_158>, (CENTRAL_S06142, archive_subject_520): <SubjectData archive_subject_520>}>


## Getting user information

You can get some information about the users on the server using the REST API:

In [24]:
print(session.users['xnatpydemo'])
print(session.users['xnatpydemo'].first_name)
print(session.users['xnatpydemo'].email)

<User xnatpydemo [1830]>
xnatpy
hakim.achterberg@gmail.com


## Inspect (similar to pyxnat)

There is also an inspect module similar to that of pyxnat. It allows you to list datatypes and search fields defined on the server:

In [25]:
print('== Datatypes ==')
print(session.inspect.datatypes())
print('== Data fields ==')
print(session.inspect.datafields('xnat:subjectData'))

== Datatypes ==
[u'xnat:qcAssessmentData', u'fs:aparcRegionAnalysis', u'wrk:workflowData', u'xnat:investigatorData', u'fs:automaticSegmentationData', u'fs:asegRegionAnalysis', u'cnda:manualVolumetryData', u'genetics:geneticTestResults', u'cnda:clinicalAssessmentData', u'fs:fsData', u'cnda:psychometricsData', u'xnat:subjectData', u'cnda:dtiData', u'cnda:atlasScalingFactorData', u'xnat:rtSessionData', u'sf:encounterLog', u'xnat:petSessionData', u'neurocog:symptomsNeurocog', u'xnat:mrSessionData', u'cnda:segmentationFastData', u'sapssans:symptomsSAPSSANS', u'adrc:ADRCClinicalData', u'xnat:ctSessionData', u'xnat:usSessionData', u'pup:pupTimeCourseData', u'xnat:projectData', u'cnda:radiologyReadData', u'cnda:modifiedScheltensData']
== Data fields ==
[u'xnat:subjectData/INSERT_DATE', u'xnat:subjectData/INSERT_USER', u'xnat:subjectData/GENDER_TEXT', u'xnat:subjectData/HANDEDNESS_TEXT', u'xnat:subjectData/DOB', u'xnat:subjectData/EDUC', u'xnat:subjectData/SES', u'xnat:subjectData/INVEST_CSV', 

## Close the session!

In [ ]:
# Don't forget to disconnect to close cleanly and clean up temporary things!
session.disconnect()

## Context operator

It is also possible to use xnatpy in a context, which guarantees clean closure of the connections etc.

In [ ]:
with xnat.connect('https://central.xnat.org', user='xnatpydemo', password='demo2017') as session:
    print('Nosetests project description: {}'.format(session.projects['xnatpydemo'].description))
    
# Here the session will be closed properly, even if there were exceptions within the `with` context

## Ideas for the future

Currently I am thinking on two different additions and how to implement that best.
* Creation of new objects
* XNAT searches

This illustrates my current ideas, but these are not implemented yet. If you have an opinion about this, let me know!

#### Object creation

or alternatively

#### Searches

The idea is to create something similar to SQLAlchemy

This sort of works:

In [26]:
with xnat.connect('https://central.xnat.org', user='xnatpydemo', password='demo2017') as session:
    print session.classes.SubjectData.query().filter(session.classes.SubjectData.initials == 'JC').all()

[{'insert_user': 'xnatpydemo', 'subject_label': 'subject001', 'ses': '', 'insert_date': '2017-10-15 08:56:12.551', 'dob': '', 'gender': 'male', 'handedness': 'left', 'quarantine_status': 'active', 'subjectid': 'CENTRAL_S06137', 'project': 'xnatpydemo', 'educ': '', 'projects': ',<xnatpydemo>'}]


But this does not: